In [1]:
#importing the necessary libraries

import numpy as np
import pandas as pd
from bs4 import BeautifulSoup
import requests
print('import successful')

import successful


**Firstly, we process the Canada data. The company's original location is Rosdale in Toronto. We first examine the data from Rosedale and the surrounding areas in Toronto.**

In [2]:
#obtaining the wikipedia page and using lxml parser
source = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text
soup = BeautifulSoup(source, 'lxml')

In [213]:
print(soup.title)

<title>List of postal codes of Canada: M - Wikipedia</title>


Using the BeautifulSoup library to parse the data from the postcode table in the webpage, as we can see the required elements are separated by 'td' tags

In [3]:
postcode_table = soup.find('table', class_= 'wikitable sortable')
table_elements = postcode_table.findAll('td')
print(table_elements[:20])

[<td>M1A</td>, <td>Not assigned</td>, <td>Not assigned
</td>, <td>M2A</td>, <td>Not assigned</td>, <td>Not assigned
</td>, <td>M3A</td>, <td><a href="/wiki/North_York" title="North York">North York</a></td>, <td><a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>
</td>, <td>M4A</td>, <td><a href="/wiki/North_York" title="North York">North York</a></td>, <td><a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>
</td>, <td>M5A</td>, <td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>, <td><a href="/wiki/Harbourfront_(Toronto)" title="Harbourfront (Toronto)">Harbourfront</a>
</td>, <td>M5A</td>, <td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>, <td><a href="/wiki/Regent_Park" title="Regent Park">Regent Park</a>
</td>, <td>M6A</td>, <td><a href="/wiki/North_York" title="North York">North York</a></td>]


In [4]:
len(table_elements) #finding the total number of elements in the table

867

Using a for-loop to split the table elements into separate rows, where the first,second and third elements of each row corresponds to postcode, bourogh and neighbourhood respectively. All the rows are combined to form the list: data_table

In [5]:
data_table=[]
for i in range(0, 867, 3):
    split_table_in_columns = [[table_elements[i], table_elements[i+1], table_elements[i+2]] ]
    postcode = table_elements[i].text.strip()
    bourough = table_elements[i+1].text.strip()
    neighbourhood = table_elements[i+2].text.strip()
    data_table.append([postcode, bourough, neighbourhood])
data_table

[['M1A', 'Not assigned', 'Not assigned'],
 ['M2A', 'Not assigned', 'Not assigned'],
 ['M3A', 'North York', 'Parkwoods'],
 ['M4A', 'North York', 'Victoria Village'],
 ['M5A', 'Downtown Toronto', 'Harbourfront'],
 ['M5A', 'Downtown Toronto', 'Regent Park'],
 ['M6A', 'North York', 'Lawrence Heights'],
 ['M6A', 'North York', 'Lawrence Manor'],
 ['M7A', "Queen's Park", 'Not assigned'],
 ['M8A', 'Not assigned', 'Not assigned'],
 ['M9A', 'Etobicoke', 'Islington Avenue'],
 ['M1B', 'Scarborough', 'Rouge'],
 ['M1B', 'Scarborough', 'Malvern'],
 ['M2B', 'Not assigned', 'Not assigned'],
 ['M3B', 'North York', 'Don Mills North'],
 ['M4B', 'East York', 'Woodbine Gardens'],
 ['M4B', 'East York', 'Parkview Hill'],
 ['M5B', 'Downtown Toronto', 'Ryerson'],
 ['M5B', 'Downtown Toronto', 'Garden District'],
 ['M6B', 'North York', 'Glencairn'],
 ['M7B', 'Not assigned', 'Not assigned'],
 ['M8B', 'Not assigned', 'Not assigned'],
 ['M9B', 'Etobicoke', 'Cloverdale'],
 ['M9B', 'Etobicoke', 'Islington'],
 ['M9B', 

The data_table is cast into a pandas dataframe, and the columns are named

In [7]:
df_CanadaPostcodes = pd.DataFrame(data_table)
df_CanadaPostcodes.columns = ['Postcode', 'Bourough', 'Neighbourhood']
df_CanadaPostcodes.head(10)


Postcode          Bourough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M5A  Downtown Toronto       Regent Park
6      M6A        North York  Lawrence Heights
7      M6A        North York    Lawrence Manor
8      M7A      Queen's Park      Not assigned
9      M8A      Not assigned      Not assigned

In [8]:
df_CanadaPostcodes.shape #checking the dimensions of the dataframe

(289, 3)

Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned, and the corresponding rows are removed from the dataframe

In [9]:
df_CanadaPostcodes = df_CanadaPostcodes[~df_CanadaPostcodes['Bourough'].isin(['Not assigned'])]
df_CanadaPostcodes.reset_index(inplace=True)
df_CanadaPostcodes.drop('index', axis=1, inplace=True)
df_CanadaPostcodes.head(10)


Postcode          Bourough     Neighbourhood
0      M3A        North York         Parkwoods
1      M4A        North York  Victoria Village
2      M5A  Downtown Toronto      Harbourfront
3      M5A  Downtown Toronto       Regent Park
4      M6A        North York  Lawrence Heights
5      M6A        North York    Lawrence Manor
6      M7A      Queen's Park      Not assigned
7      M9A         Etobicoke  Islington Avenue
8      M1B       Scarborough             Rouge
9      M1B       Scarborough           Malvern

In [10]:
df_CanadaPostcodes.shape #checking the dimensions of the dataframe

(212, 3)

More than one neighborhood can exist in one postal code area as can be seen from the above dataframe. For example, in the table on the Wikipedia page, we will notice that M5A is listed twice and has two neighborhoods: Harbourfront and Regent Park. These two rows will be combined into one row with the neighborhoods separated with a comma in the below dataframe. This is done by using the groupby method on Postcode and Bourough, and using the join method to combine the neighbourhoods (saparated by commas) having same values of Postcode and Bourough

In [11]:
df_CanadaPostcodes = df_CanadaPostcodes.groupby(['Postcode','Bourough'])['Neighbourhood'].apply(', '.join).reset_index()
df_CanadaPostcodes.head()

Postcode     Bourough                           Neighbourhood
0      M1B  Scarborough                          Rouge, Malvern
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union
2      M1E  Scarborough       Guildwood, Morningside, West Hill
3      M1G  Scarborough                                  Woburn
4      M1H  Scarborough                               Cedarbrae

If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough. So for the 9th cell in the table on the Wikipedia page, the value of the Borough and the Neighborhood columns will be Queen's Park.

In [12]:
missing_neighbourhoods = df_CanadaPostcodes.Neighbourhood.values == 'Not assigned'
df_CanadaPostcodes.Neighbourhood[missing_neighbourhoods] = df_CanadaPostcodes.Bourough[missing_neighbourhoods]
df_CanadaPostcodes.head()

Postcode     Bourough                           Neighbourhood
0      M1B  Scarborough                          Rouge, Malvern
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union
2      M1E  Scarborough       Guildwood, Morningside, West Hill
3      M1G  Scarborough                                  Woburn
4      M1H  Scarborough                               Cedarbrae

In [13]:
df_CanadaPostcodes.shape #checking the dimensions of the dataframe

(103, 3)

In [14]:
#importing the csv file that has the geographical coordinates of each postal code and casting it into a new pandas dataframe called geo_data
urlfordata="http://cocl.us/Geospatial_data" 
geo_data=pd.read_csv(urlfordata)
geo_data.head(10)

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476
5         M1J  43.744734 -79.239476
6         M1K  43.727929 -79.262029
7         M1L  43.711112 -79.284577
8         M1M  43.716316 -79.239476
9         M1N  43.692657 -79.264848

In [15]:
df_CanadaPostcodes.rename(columns={'Postcode': 'Postal Code'}, inplace=True)#renaming the first column in the first dataframe to match the second dataframe
df_CanadaPostcodes.head()

Postal Code     Bourough                           Neighbourhood
0         M1B  Scarborough                          Rouge, Malvern
1         M1C  Scarborough  Highland Creek, Rouge Hill, Port Union
2         M1E  Scarborough       Guildwood, Morningside, West Hill
3         M1G  Scarborough                                  Woburn
4         M1H  Scarborough                               Cedarbrae

The two dataframes are now merged in order to create a new dataframe. The new dataframe displays the postal code of each neighborhood along with the borough name and neighborhood name, and the latitude and the longitude coordinates of each neighborhood.

In [16]:
final_df=pd.merge(df_CanadaPostcodes, geo_data, on='Postal Code')
final_df.head()

Postal Code     Bourough                           Neighbourhood   Latitude  \
0         M1B  Scarborough                          Rouge, Malvern  43.806686   
1         M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2         M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3         M1G  Scarborough                                  Woburn  43.770992   
4         M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [17]:
#importing the libraries necessary for analysis

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.0.2p             |       h470a237_1         3.1 MB  conda-forge
    certifi-2018.10.15         |        py36_1000         138 KB  conda-forge
    geopy-1.17.0               |             py_0          49 KB  conda-forge
    ca-certificates-2018.10.15 |       ha4d7672_0         135 KB  conda-forge
    conda-4.5.11               |        py36_1000         651 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         4.1 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0            conda-forge
    geopy:           

In [18]:
##Use geopy library to get the latitude and longitude values of Toronto City.

address = 'Toronto'
geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto City are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/lib/python3.6/site-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of Toronto City are 43.653963, -79.387207.


**new dataframe only for Toronto**

In [19]:
toronto_df = final_df[final_df['Bourough'].str.contains("Toronto")].reset_index(drop=True)

In [20]:
toronto_df.head()

Postal Code         Bourough                   Neighbourhood   Latitude  \
0         M4E     East Toronto                     The Beaches  43.676357   
1         M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2         M4L     East Toronto  The Beaches West, India Bazaar  43.668999   
3         M4M     East Toronto                 Studio District  43.659526   
4         M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [21]:
toronto_df.shape

(38, 5)

In [22]:
toronto_df.rename(columns={'Bourough': 'Area'}, inplace=True)
toronto_df.set_index('Neighbourhood', drop=True, inplace=True)
toronto_df.head()

Postal Code             Area   Latitude  \
Neighbourhood                                                            
The Beaches                            M4E     East Toronto  43.676357   
The Danforth West, Riverdale           M4K     East Toronto  43.679557   
The Beaches West, India Bazaar         M4L     East Toronto  43.668999   
Studio District                        M4M     East Toronto  43.659526   
Lawrence Park                          M4N  Central Toronto  43.728020   

                                Longitude  
Neighbourhood                              
The Beaches                    -79.293031  
The Danforth West, Riverdale   -79.352188  
The Beaches West, India Bazaar -79.315572  
Studio District                -79.340923  
Lawrence Park                  -79.388790

In [23]:
original_loc = toronto_df.loc['Rosedale', :].copy()
original_loc['Area'] = 'Rosedale'
original_loc = original_loc.drop(labels=['Postal Code'])
original_loc

Area         Rosedale
Latitude      43.6796
Longitude    -79.3775
Name: Rosedale, dtype: object

**Next, we start processing the Melbourne data.**

In [29]:
#obtaining the wikipedia page and using lxml parser
source = requests.get('https://en.wikipedia.org/wiki/Postal_district_numbers_of_Melbourne').text
soup = BeautifulSoup(source, 'lxml')

In [30]:
print(soup.title)

<title>Postal district numbers of Melbourne - Wikipedia</title>


In [31]:
postcode_table = soup.find('table', class_= 'wikitable sortable')
table_elements = postcode_table.findAll('td')
print(table_elements[:50])

[<td>(Carnegie North)</td>, <td>SE.10</td>, <td></td>, <td></td>, <td>* no Post Office
</td>, <td>(Hawthorn East)</td>, <td>E. 3</td>, <td></td>, <td></td>, <td>* no Post Office
</td>, <td>(Williamstown West)</td>, <td>W.17</td>, <td></td>, <td></td>, <td>* no Post Office
</td>, <td>Abbotsford</td>, <td>N. 9</td>, <td>1928</td>, <td><a href="/wiki/Abbotsford,_Victoria" title="Abbotsford, Victoria">Abbotsford</a></td>, <td>** name of district
</td>, <td><a href="/wiki/Essendon_Airport" title="Essendon Airport">Aerodrome Essendon</a></td>, <td>W. 6</td>, <td>1938</td>, <td><a href="/wiki/Essendon,_Victoria" title="Essendon, Victoria">Essendon</a></td>, <td>.
</td>, <td>Albert Park</td>, <td>SC. 6</td>, <td>1928</td>, <td><a href="/wiki/Albert_Park,_Victoria" title="Albert Park, Victoria">Albert Park</a></td>, <td>*
</td>, <td>Albert Park South</td>, <td>SC. 6</td>, <td>1947</td>, <td><a href="/wiki/Albert_Park,_Victoria" title="Albert Park, Victoria">Albert Park</a></td>, <td>.
</td>, <t

In [32]:
len(table_elements) #finding the total number of elements in the table

1790

In [33]:
data_table=[]
for i in range(0, 1790, 5):
    split_table_in_columns = [[table_elements[i], table_elements[i+1], table_elements[i+2],table_elements[i+3],table_elements[i+4]] ]
    locality = table_elements[i].text.strip()
    suburb = table_elements[i+3].text.strip()
    data_table.append([locality, suburb])
data_table

[['(Carnegie North)', ''],
 ['(Hawthorn East)', ''],
 ['(Williamstown West)', ''],
 ['Abbotsford', 'Abbotsford'],
 ['Aerodrome Essendon', 'Essendon'],
 ['Albert Park', 'Albert Park'],
 ['Albert Park South', 'Albert Park'],
 ['Alphington', 'Alphington'],
 ['Altona', 'Altona'],
 ['Altona East', 'Altona North'],
 ['Altona North', 'Altona North'],
 ['Argyle Street', 'Footscray West'],
 ['Armadale', 'Armadale'],
 ['Armadale North', 'Armadale'],
 ['Ascot Vale', 'Ascot Vale'],
 ['Ascot Vale East', 'Ascot Vale'],
 ['Ascot Vale RAAF', 'Ascot Vale'],
 ['Ascot Vale West', 'Ascot Vale'],
 ['Ashburton', 'Ashburton'],
 ['Ashburton East', 'Ashburton'],
 ['Ashwood', 'Ashwood'],
 ['Aspendale', 'Aspendale'],
 ['Auburn', 'Hawthorn East'],
 ['Auburn South', 'Hawthorn'],
 ['Balaclava', 'Balaclava'],
 ['Balwyn', 'Balwyn'],
 ['Balwyn East', 'Balwyn'],
 ['Balwyn North', 'Balwyn North'],
 ['Balwyn West', ''],
 ['Barker', 'Hawthorn'],
 ['Batman', 'Coburg North'],
 ['Beaumaris', 'Beaumaris'],
 ['Beaumaris South'

In [34]:
df_MelbourneArea = pd.DataFrame(data_table)
df_MelbourneArea.columns = ['Area', 'Suburb']
df_MelbourneArea.head(10)


Area        Suburb
0     (Carnegie North)              
1      (Hawthorn East)              
2  (Williamstown West)              
3           Abbotsford    Abbotsford
4   Aerodrome Essendon      Essendon
5          Albert Park   Albert Park
6    Albert Park South   Albert Park
7           Alphington    Alphington
8               Altona        Altona
9          Altona East  Altona North

If a cell has a locality but a Not assigned suburb, then the suburb will be the same as the locality.Also for consistency in the two dataframes the commas present in any locality names are removed.

In [35]:
missing_suburbs = df_MelbourneArea.Suburb.values == ''
df_MelbourneArea.Suburb[missing_suburbs] = df_MelbourneArea.Area[missing_suburbs]
#df_MelbourneArea=df_MelbourneArea.Area.replace({'Were Street, Brighton': 'Were Street Brighton','Geelong Road, Footscray':'Geelong Road Footscray','North Road, Brighton':'North Road Brighton',"St George's Road, Thornbury":"St George's Road Thornbury"})
df_MelbourneArea = pd.DataFrame(df_MelbourneArea)
df_MelbourneArea.head()

Area               Suburb
0     (Carnegie North)     (Carnegie North)
1      (Hawthorn East)      (Hawthorn East)
2  (Williamstown West)  (Williamstown West)
3           Abbotsford           Abbotsford
4   Aerodrome Essendon             Essendon

In [36]:
#importing the csv file that has the geographical coordinates of each postal code and casting it into a new pandas dataframe called geo_data
geo_data=pd.read_excel("geocode.xls",)
geo_data.columns = ['Area', 'Latitude','Longitude']
geo_data.head()

Area   Latitude   Longitude
0     (Carnegie North) -37.884829  145.058806
1      (Hawthorn East) -37.831000  145.050000
2  (Williamstown West) -37.808000  144.927000
3           Abbotsford -37.803000  145.002000
4   Aerodrome Essendon -37.726410  144.901488

The two dataframes are now merged in order to create a new dataframe. The new dataframe displays the postal code of each locality along with the suburb name, and the latitude and the longitude coordinates of each locality.

In [37]:
final_df=pd.merge(df_MelbourneArea, geo_data, on='Area')
final_df.head()

Area               Suburb   Latitude   Longitude
0     (Carnegie North)     (Carnegie North) -37.884829  145.058806
1      (Hawthorn East)      (Hawthorn East) -37.831000  145.050000
2  (Williamstown West)  (Williamstown West) -37.808000  144.927000
3           Abbotsford           Abbotsford -37.803000  145.002000
4   Aerodrome Essendon             Essendon -37.726410  144.901488

In [38]:
#the rows which do not have the latitude-longitude values are removed from the list
final_df=final_df[final_df.Latitude != 0]
final_df.shape

(350, 4)

In [39]:
#A new dataframe consisting only of the locality column from the final_df dataframe is created for test purposes, to check the rows which do not appear in the new dataframe populated by Foursquare later 
final_dftest=final_df[['Area']]

In [40]:
final_dftest.shape

(350, 1)

In [41]:
##Use geopy library to get the latitude and longitude values of Melbourne City.

address = 'Melbourne, Australia'
geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Melbourne City are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/lib/python3.6/site-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of Melbourne City are -37.8142176, 144.9631608.


In [42]:
# create map of Melbourne using latitude and longitude values
map_Melbourne = folium.Map(location=[latitude, longitude], zoom_start=10)

In [43]:
# add markers to map
for lat, lng, area, suburb in zip(final_df['Latitude'], final_df['Longitude'], final_df['Area'], final_df['Suburb']):
    label = '{}, {}'.format(locality, suburb)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Melbourne)  
    
map_Melbourne

**Next we do the analysis by comparing Rosedale, Toronto with the localities of Melbourne**

In [44]:
#renaming the Locality column in the Melbourne dataframe as Area and removing the suburb column for consistency
del final_df['Suburb']
final_df

Area   Latitude   Longitude
0                (Carnegie North) -37.884829  145.058806
1                 (Hawthorn East) -37.831000  145.050000
2             (Williamstown West) -37.808000  144.927000
3                      Abbotsford -37.803000  145.002000
4              Aerodrome Essendon -37.726410  144.901488
5                     Albert Park -37.842000  144.950000
6               Albert Park South -37.835000  144.960000
7                      Alphington -37.780000  145.023000
8                          Altona -37.868000  144.830000
9                     Altona East -37.847104  144.856394
10                   Altona North -37.841000  144.849000
11                  Argyle Street -37.797660  144.979716
12                       Armadale -37.857000  145.021000
13                 Armadale North -37.857000  145.021000
14                     Ascot Vale -37.779000  144.919000
15                Ascot Vale East -37.779000  144.919000
16                Ascot Vale RAAF -37.760044  144.925405
17                Ascot Vale West -37.780643  144.911184
18                      Ashburton -37.866944  145.083056
19                 Ashburton East -37.813000  144.985000
20                        Ashwood -37.867000  145.103000
21                      Aspendale -38.025000  145.104000
22                         Auburn -37.822485  145.045896
23                   Auburn South -37.839522  145.045557
24                      Balaclava -37.873000  144.993000
25                         Balwyn -37.808889  145.078889
26                    Balwyn East -37.813000  144.985000
27                   Balwyn North -37.793611  145.086389
28                    Balwyn West -37.808889  145.078889
29                         Barker  28.097827  -80.680548
30                         Batman -37.821760  144.957243
31                      Beaumaris -37.983000  145.043400
32                Beaumaris South -37.986479  145.033904
33                        Beevers -37.813628  144.963058
34                      Bentleigh -37.922000  145.036000
35              Bentleigh Central -37.922000  145.036000
36                 Bentleigh East -37.921000  145.067000
37                Bentleigh North -37.922000  145.036000
38                     Black Rock -37.972000  145.021000
39               Black Rock North -37.966993  145.017093
40                    Booran Road -37.892671  145.036937
41             Bourke Street East -37.811647  144.972064
42                       Box Hill -37.821500  145.126000
43                 Box Hill North -37.807000  145.120000
44                 Box Hill South -37.836000  145.124000
45                      Braybrook -37.786000  144.856000
46                Braybrook North -37.786000  144.856000
47                       Brighton -37.905000  144.996000
48                 Brighton Beach -37.915968  144.986140
49                  Brighton East -37.916000  145.015000
50                  Brighton Road -37.875824  144.992071
51                  Brighton West  28.089278  -80.696844
52                      Brunswick -37.766700  144.962800
53                 Brunswick East -37.776000  144.974000
54                Brunswick North  28.124641  -80.670081
55                Brunswick South -37.778654  144.972978
56                 Brunswick West -37.761000  144.943000
57                     Burke Road -37.828080  145.057350
58                        Burnley -37.829926  145.017647
59                  Burnley North -37.829926  145.017647
60                        Burwood -37.850000  145.114000
61                   Burwood East -37.852000  145.150000
62                   Burwood West -37.867871  145.231759
63                     Camberwell -37.835000  145.071000
64                Camberwell East -37.813000  144.985000
65               Camberwell North -37.824340  145.058217
66               Camberwell South -37.847747  145.062178
67                      Camp Pell -37.813628  144.963058
68                     Canterbury -37.825000  145.078000
69                        Carlton -37.8

**Define Foursquare Credentials and Version**

In [219]:
CLIENT_ID = 'O3HJWO2SQD20SWIOPJI5YJJ0S12BVGDGMCNVOE3JC5HJN***'  # your Foursquare ID
CLIENT_SECRET = '3WU4HW4ULJEUR3TZWCZARUA1ZL0S5JCUP23XXKKR4FXHN***' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: O3HJWO2SQD20SWIOPJI5YJJ0S12BVGDGMCNVOE3JC5HJN***
CLIENT_SECRET:3WU4HW4ULJEUR3TZWCZARUA1ZL0S5JCUP23XXKKR4FXHN***


Exploring the first neighborhood in our Melbourne dataframe.

In [146]:
final_df.loc[0, 'Area']

'(Carnegie North)'

Get the neighborhood's latitude and longitude values.

In [147]:
locality_latitude = final_df.loc[0, 'Latitude'] # locality latitude value
locality_longitude = final_df.loc[0, 'Longitude'] # locality longitude value

locality_name = final_df.loc[0, 'Area'] # locality name

print('Latitude and longitude values of {} are {}, {}.'.format(locality_name, 
                                                               locality_latitude, 
                                                               locality_longitude))

Latitude and longitude values of (Carnegie North) are -37.884829, 145.058806.


Now, let's get the top 100 venues that are in 'Carnegie North' within a radius of 500 meters.

In [148]:

LIMIT = 100 
radius = 500

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    locality_latitude, 
    locality_longitude, 
    radius, 
    LIMIT)

url

'https://api.foursquare.com/v2/venues/explore?&client_id=W0LJ1BATE0QXL1LOLJ5PB4K3WEJUPATDA4OUGB1JGUSVU5BC&client_secret=ME5XFNHIHS3YUQUXJMVGEABNLDJM5SH4L2IFH10HGJDWIZTB&v=20180605&ll=-37.884829,145.058806&radius=500&limit=100'

In [149]:
results = requests.get(url).json()

In [150]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a pandas dataframe.

In [151]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name           categories        lat         lng
0                    Grill'd         Burger Joint -37.887390  145.057494
1  Shyun Japanese Restaurant  Japanese Restaurant -37.888466  145.057225
2               Huff Bagelry           Bagel Shop -37.888168  145.057269
3            Mrs Kim's Grill    Korean Restaurant -37.888670  145.057160
4                 Platform 3       Breakfast Spot -37.885513  145.057592

In [152]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

33 venues were returned by Foursquare.


**Explore Neighborhoods**

We create a function to repeat the same process to all the neighborhoods in Melbourne

In [153]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
  
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Area', 
                  'Locality Latitude', 
                  'Locality Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [154]:
#we explore the Rosedale, Toronto neighbourhood
original_venues = getNearbyVenues(names=[original_loc['Area']], 
                                 latitudes=[original_loc['Latitude']], 
                                 longitudes=[original_loc['Longitude']], 
                                 radius = 500)
original_venues.head()

Rosedale


Area  Locality Latitude  Locality Longitude                 Venue  \
0  Rosedale          43.679563          -79.377529         Rosedale Park   
1  Rosedale          43.679563          -79.377529          Whitney Park   
2  Rosedale          43.679563          -79.377529  Alex Murray Parkette   
3  Rosedale          43.679563          -79.377529        Milkman's Lane   

   Venue Latitude  Venue Longitude Venue Category  
0       43.682328       -79.378934     Playground  
1       43.682036       -79.373788           Park  
2       43.678300       -79.382773           Park  
3       43.676352       -79.373842          Trail

Now we write the code to run the above function on each neighborhood and create a new dataframe called melbourne_venues.

In [155]:
melbourne_venues = getNearbyVenues(names=final_df['Area'],
                                   latitudes=final_df['Latitude'],
                                   longitudes=final_df['Longitude']
                                  )

(Carnegie North)
(Hawthorn East)
(Williamstown West)
Abbotsford
Aerodrome Essendon
Albert Park
Albert Park South
Alphington
Altona
Altona East
Altona North
Argyle Street
Armadale
Armadale North
Ascot Vale
Ascot Vale East
Ascot Vale RAAF
Ascot Vale West
Ashburton
Ashburton East
Ashwood
Aspendale
Auburn
Auburn South
Balaclava
Balwyn
Balwyn East
Balwyn North
Balwyn West
Barker
Batman
Beaumaris
Beaumaris South
Beevers
Bentleigh
Bentleigh Central
Bentleigh East
Bentleigh North
Black Rock
Black Rock North
Booran Road
Bourke Street East
Box Hill
Box Hill North
Box Hill South
Braybrook
Braybrook North
Brighton
Brighton Beach
Brighton East
Brighton Road
Brighton West
Brunswick
Brunswick East
Brunswick North
Brunswick South
Brunswick West
Burke Road
Burnley
Burnley North
Burwood
Burwood East
Burwood West
Camberwell
Camberwell East
Camberwell North
Camberwell South
Camp Pell
Canterbury
Carlton
Carlton North
Carlton South
Carnegie
Carnegie South
Caulfield
Caulfield East
Caulfield Junction
Caulfiel

In [56]:
melbourne_venues.head(10)

Area  Locality Latitude  Locality Longitude  \
0  (Carnegie North)         -37.884829          145.058806   
1  (Carnegie North)         -37.884829          145.058806   
2  (Carnegie North)         -37.884829          145.058806   
3  (Carnegie North)         -37.884829          145.058806   
4  (Carnegie North)         -37.884829          145.058806   
5  (Carnegie North)         -37.884829          145.058806   
6  (Carnegie North)         -37.884829          145.058806   
7  (Carnegie North)         -37.884829          145.058806   
8  (Carnegie North)         -37.884829          145.058806   
9  (Carnegie North)         -37.884829          145.058806   

                           Venue  Venue Latitude  Venue Longitude  \
0                        Grill'd      -37.887390       145.057494   
1      Shyun Japanese Restaurant      -37.888466       145.057225   
2                   Huff Bagelry      -37.888168       145.057269   
3                Mrs Kim's Grill      -37.888670       145.057160   
4                     Platform 3      -37.885513       145.057592   
5                     Woolworths      -37.884373       145.058391   
6                      Paradai I      -37.886911       145.057432   
7  Auntie's Dumplings Restaurant      -37.886917       145.057495   
8         Eastern Dumpling House      -37.888608       145.057200   
9                Gabriella Pizza      -37.888922       145.057095   

        Venue Category  
0         Burger Joint  
1  Japanese Restaurant  
2           Bagel Shop  
3    Korean Restaurant  
4       Breakfast Spot  
5          Supermarket  
6      Thai Restaurant  
7  Dumpling Restaurant  
8  Dumpling Restaurant  
9          Pizza Place

In [57]:
# we check the size of the resulting dataframe
print(melbourne_venues.shape)


(8197, 7)


In [58]:

all_venues = melbourne_venues.copy()
all_venues = pd.concat([all_venues, original_venues])
all_venues.shape

(8201, 7)

In [59]:
all_venuesgroup = all_venues.groupby('Area').count().reset_index()# check how many venues were returned for each locality

In [60]:
all_venuesgroup

Area  Locality Latitude  Locality Longitude  \
0                (Carnegie North)                 33                  33   
1                 (Hawthorn East)                  9                   9   
2           (St Kilda Road North)                 32                  32   
3           (St Kilda Road South)                 32                  32   
4             (Williamstown West)                  2                   2   
5                      Abbotsford                 17                  17   
6              Aerodrome Essendon                  4                   4   
7                     Albert Park                 31                  31   
8               Albert Park South                 65                  65   
9                      Alphington                 13                  13   
10                         Altona                 12                  12   
11                    Altona East                  1                   1   
12                   Altona North                  1                   1   
13                  Argyle Street                100                 100   
14                       Armadale                 19                  19   
15                 Armadale North                 19                  19   
16                     Ascot Vale                 20                  20   
17                Ascot Vale East                 20                  20   
18                Ascot Vale RAAF                  4                   4   
19                Ascot Vale West                 11                  11   
20                      Ashburton                  7                   7   
21                 Ashburton East                 29                  29   
22                        Ashwood                  4                   4   
23                      Aspendale                  5                   5   
24                         Auburn                 10                  10   
25                   Auburn South                  6                   6   
26                      Balaclava                 35                  35   
27                         Balwyn                  8                   8   
28                    Balwyn East                 29                  29   
29                   Balwyn North                  3                   3   
30                    Balwyn West                  8                   8   
31                         Barker                  4                   4   
32                         Batman                 86                  86   
33                      Beaumaris                  6                   6   
34                Beaumaris South                 11                  11   
35                        Beevers                100                 100   
36                      Bentleigh                 18                  18   
37              Bentleigh Central                 18                  18   
38                 Bentleigh East                  1                   1   
39                Bentleigh North                 18                  18   
40                     Black Rock                  6                   6   
41               Black Rock North                  1                   1   
42                    Booran Road                  4                   4   
43             Bourke Street East                100                 100   
44                       Box Hill                 48                  48   
45                 Box Hill North                  4                   4   
46                 Box Hill South                  4                   4   
47                      Braybrook                  3                   3   
48                Braybrook North                  3                   3   
49                       Brighton                  7                   7   
50                 Brighton Beach                  5                   5   
51                  Brighton East                  8                   8   
5

Let's find out how many unique categories can be curated from all the returned venues

In [61]:
print('There are {} uniques categories.'.format(len(all_venues['Venue Category'].unique())))

There are 313 uniques categories.


In [62]:
all_venuesgroup.shape

(347, 7)

In [63]:
#creating a test dataframe to find those rows in the final_dftest created earlier which are not present in the melbourne_venuesgroup 
all_venuesgrouptest=all_venuesgroup[['Area']]

In [64]:
all_venuesgrouptest.shape

(347, 1)

In [65]:
#finding the rows present in the final_df dataframe but missing in the melbourne_venuesgroup dataframe with values returned by Foursquare
df = pd.concat([final_dftest, all_venuesgrouptest])
df = df.reset_index(drop=True)
df_gpby = df.groupby(list(df.columns))
idx = [x[0] for x in df_gpby.groups.values() if len(x) == 1]
df.reindex(idx)

Area
150           Gardiner
166           Hartwell
211  Melbourne Airport
256     Oakleigh South
639           Rosedale

In [66]:
final_df = final_df.drop(final_df.index[[150,166,211,256]]) #these rows are removed for consistency

In [67]:
final_df.shape

(346, 3)

In [68]:
all_data = final_df.copy()
original_loc.name = len(all_data)
all_data = pd.concat([all_data, original_loc.to_frame().T])
all_data.shape

(347, 3)

**Analyze Each Neighborhood**

In [69]:

# one hot encoding
all_onehot = pd.get_dummies(all_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
all_onehot['Area'] = all_venues['Area'] 

# move neighborhood column to the first column
fixed_columns = [all_onehot.columns[-1]] + list(all_onehot.columns[:-1])
all_onehot = all_onehot[fixed_columns]

all_onehot.head()

Area  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  (Carnegie North)                  0               0                  0   
1  (Carnegie North)                  0               0                  0   
2  (Carnegie North)                  0               0                  0   
3  (Carnegie North)                  0               0                  0   
4  (Carnegie North)                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Aquarium  \
0                   0                    0             0         0   
1                   0                    0             0         0   
2                   0                    0             0         0   
3                   0                    0             0         0   
4                   0                    0             0         0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Arts & Crafts Store  \
0                 0                       0            0                    0   
1                 0                       0            0                    0   
2                 0                       0            0                    0   
3                 0                       0            0                    0   
4                 0                       0            0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Australian Restaurant  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                      0          0           0       0     0    0   
1                      0          0           0       0     0    0   
2                      0          0           1       0     0    0   
3                      0          0           0       0     0    0   
4                      0          0           0       0     0    0   

   Basketball Court  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0                 0      0                0         0            0   
1                 0      0                0         0            0   
2                 0      0                0         0            0   
3                 0      0                0         0            0   
4                 0      0                0         0            0   

   Big Box Store  Bike Rental / Bike Share  Bistro  Board Shop  \
0              0                         0       0           0   
1              0                         0       0           0   
2              0                         0       0           0   
3              0                         0       0           0   
4              0                         0       0           0   

   Boarding House  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0               0          0                 0         0              0   
1               0          0                 0         0              0   
2               0          0                 0         0              0   
3               0          0                 0         0              0   
4               0          0                 0         0              0   

   Bowling Green  Brazilian Restaurant  Breakfast Spot  Brewery  Bridge  \
0              0                     0               0        0       0   
1              0                     0               0        0       0   
2              0                     0               0        0       0   
3              0                     0               0        0       0   
4              0                     0               1        0       0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0                0       0       

In [70]:
all_onehot.shape

(8201, 314)

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category and confirm the new size

In [71]:
all_grouped = all_onehot.groupby('Area').mean().reset_index()
all_grouped

Area  Accessories Store  Adult Boutique  \
0                (Carnegie North)           0.000000        0.000000   
1                 (Hawthorn East)           0.000000        0.000000   
2           (St Kilda Road North)           0.000000        0.000000   
3           (St Kilda Road South)           0.000000        0.000000   
4             (Williamstown West)           0.000000        0.000000   
5                      Abbotsford           0.000000        0.000000   
6              Aerodrome Essendon           0.000000        0.000000   
7                     Albert Park           0.000000        0.000000   
8               Albert Park South           0.000000        0.000000   
9                      Alphington           0.000000        0.000000   
10                         Altona           0.000000        0.000000   
11                    Altona East           0.000000        0.000000   
12                   Altona North           0.000000        0.000000   
13                  Argyle Street           0.000000        0.000000   
14                       Armadale           0.000000        0.000000   
15                 Armadale North           0.000000        0.000000   
16                     Ascot Vale           0.000000        0.000000   
17                Ascot Vale East           0.000000        0.000000   
18                Ascot Vale RAAF           0.000000        0.000000   
19                Ascot Vale West           0.000000        0.000000   
20                      Ashburton           0.000000        0.000000   
21                 Ashburton East           0.000000        0.000000   
22                        Ashwood           0.000000        0.000000   
23                      Aspendale           0.000000        0.000000   
24                         Auburn           0.000000        0.000000   
25                   Auburn South           0.000000        0.000000   
26                      Balaclava           0.000000        0.000000   
27                         Balwyn           0.000000        0.000000   
28                    Balwyn East           0.000000        0.000000   
29                   Balwyn North           0.000000        0.000000   
30                    Balwyn West           0.000000        0.000000   
31                         Barker           0.000000        0.000000   
32                         Batman           0.000000        0.000000   
33                      Beaumaris           0.000000        0.000000   
34                Beaumaris South           0.000000        0.000000   
35                        Beevers           0.000000        0.000000   
36                      Bentleigh           0.000000        0.000000   
37              Bentleigh Central           0.000000        0.000000   
38                 Bentleigh East           0.000000        0.000000   
39                Bentleigh North           0.000000        0.000000   
40                     Black Rock           0.166667        0.000000   
41               Black Rock North           0.000000        0.000000   
42                    Booran Road           0.000000        0.000000   
43             Bourke Street East           0.000000        0.000000   
44                       Box Hill           0.000000        0.000000   
45                 Box Hill North           0.000000        0.000000   
46                 Box Hill South           0.000000        0.000000   
47                      Braybrook           0.000000        0.000000   
48                Braybrook North           0.000000        0.000000   
49                       Brighton           0.000000        0.000000   
50                 Brighton Beach           0.000000        0.000000   
51                  Brighton East           0.000000        0.000000   
52                  Brighton Road           0.000000        0.000000   
53                  Brighton West           0.000000        0.000000   
54                      Brunswick           0.000000        0.000000 

In [72]:
all_grouped.shape

(347, 314)

Let's print each neighborhood along with the top 5 most common venues

In [73]:
num_top_venues = 5

for hood in all_grouped['Area']:
    print("----"+hood+"----")
    temp = all_grouped[all_grouped['Area'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----(Carnegie North)----
                 venue  freq
0    Korean Restaurant  0.06
1     Asian Restaurant  0.06
2          Supermarket  0.06
3  Dumpling Restaurant  0.06
4      Thai Restaurant  0.06


----(Hawthorn East)----
              venue  freq
0      Liquor Store  0.11
1              Park  0.11
2  Malay Restaurant  0.11
3     Movie Theater  0.11
4         Multiplex  0.11


----(St Kilda Road North)----
               venue  freq
0               Café  0.38
1              Hotel  0.19
2       Burger Joint  0.03
3  Indian Restaurant  0.03
4  Mobile Phone Shop  0.03


----(St Kilda Road South)----
               venue  freq
0               Café  0.38
1              Hotel  0.19
2       Burger Joint  0.03
3  Indian Restaurant  0.03
4  Mobile Phone Shop  0.03


----(Williamstown West)----
         venue  freq
0         Pier   0.5
1  Flea Market   0.5
2         Park   0.0
3     Pharmacy   0.0
4    Pet Store   0.0


----Abbotsford----
                 venue  freq
0                 Café  0

**We put that into a pandas dataframe**

First, let's write a function to sort the venues in descending order.

In [156]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [157]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Area']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
locality_venues_sorted = pd.DataFrame(columns=columns)
locality_venues_sorted['Area'] = all_grouped['Area']

for ind in np.arange(all_grouped.shape[0]):
    locality_venues_sorted.iloc[ind, 1:] = return_most_common_venues(all_grouped.iloc[ind, :], num_top_venues)

locality_venues_sorted

Area      1st Most Common Venue  \
0                (Carnegie North)           Malay Restaurant   
1                 (Hawthorn East)           Malay Restaurant   
2           (St Kilda Road North)                       Café   
3           (St Kilda Road South)                       Café   
4             (Williamstown West)                       Pier   
5                      Abbotsford                       Café   
6              Aerodrome Essendon             Sandwich Place   
7                     Albert Park                       Café   
8               Albert Park South                       Café   
9                      Alphington                       Café   
10                         Altona                      Beach   
11                    Altona East               Soccer Field   
12                   Altona North                  Pet Store   
13                  Argyle Street                       Café   
14                       Armadale                       Café   
15                 Armadale North                       Café   
16                     Ascot Vale         Light Rail Station   
17                Ascot Vale East         Light Rail Station   
18                Ascot Vale RAAF         Italian Restaurant   
19                Ascot Vale West                        Gym   
20                      Ashburton                       Café   
21                 Ashburton East                       Café   
22                        Ashwood                       Park   
23                      Aspendale                       Café   
24                         Auburn                       Café   
25                   Auburn South                       Park   
26                      Balaclava                       Café   
27                         Balwyn                       Café   
28                    Balwyn East                       Café   
29                   Balwyn North                        Gym   
30                    Balwyn West                       Café   
31                         Barker             Hardware Store   
32                         Batman                Coffee Shop   
33                      Beaumaris                       Café   
34                Beaumaris South                       Café   
35                        Beevers                       Café   
36                      Bentleigh                       Café   
37              Bentleigh Central                       Café   
38                 Bentleigh East                  Gift Shop   
39                Bentleigh North                       Café   
40                     Black Rock          Accessories Store   
41               Black Rock North               Dessert Shop   
42                    Booran Road                       Café   
43             Bourke Street East               Cocktail Bar   
44                       Box Hill         Chinese Restaurant   
45                 Box Hill North                       Park   
46                 Box Hill South                Golf Course   
47                      Braybrook      Vietnamese Restaurant   
48                Braybrook North      Vietnamese Restaurant   
49                       Brighton                       Café   
50                 Brighton Beach                      Beach   
51                  Brighton East         Italian Restaurant   
52                  Brighton Road                       Café   
53                  Brighton West                    Dog Run   
54                      Brunswick                       Café   
55                 Brunswick East                       Café   
56                Brunswick North             Sandwich Place   
57                Brunswick South                       Café   
58                 Brunswick West              Grocery Store   
59                     Burke Road                       Café   
60                        Burnley           Sushi Restaurant   
61                  Burnley North           Sushi Restaurant 

In [158]:
locality_venues_sorted.shape

(347, 11)

**Cluster Neighborhoods**

Run k-means to cluster the neighborhood into 5 clusters

In [159]:

# set number of clusters
kclusters = 70 #the number of clusters is chosen as 70

all_grouped_clustering = all_grouped.drop('Area', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(all_grouped_clustering)


# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([65,  2,  0,  0, 14, 22, 38,  0, 22,  0], dtype=int32)

In [160]:

all_merged = all_data.copy()

# add clustering labels
all_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
all_merged = all_merged.join(locality_venues_sorted.set_index('Area'), on='Area')

all_merged.head() # check the last columns!

Area Latitude Longitude  Cluster Labels  \
0     (Carnegie North) -37.8848   145.059              65   
1      (Hawthorn East)  -37.831    145.05               2   
2  (Williamstown West)  -37.808   144.927               0   
3           Abbotsford  -37.803   145.002               0   
4   Aerodrome Essendon -37.7264   144.901              14   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0      Malay Restaurant       Thai Restaurant   Dumpling Restaurant   
1      Malay Restaurant      Asian Restaurant                  Park   
2                  Pier           Flea Market           Zoo Exhibit   
3                  Café                   Pub        Farmers Market   
4        Sandwich Place     Recreation Center         Shopping Mall   

  4th Most Common Venue          5th Most Common Venue 6th Most Common Venue  \
0           Supermarket              Korean Restaurant      Asian Restaurant   
1          Liquor Store                      Multiplex         Movie Theater   
2               Exhibit                           Farm        Farmers Market   
3   Japanese Restaurant  Vegetarian / Vegan Restaurant     Convenience Store   
4        Gymnastics Gym              Fish & Chips Shop               Exhibit   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0   Japanese Restaurant         Train Station    Chinese Restaurant   
1                  Café           Pizza Place          Gourmet Shop   
2  Fast Food Restaurant   Filipino Restaurant     Fish & Chips Shop   
3           Coffee Shop                  Farm       Cultural Center   
4    Falafel Restaurant                  Farm        Farmers Market   

   10th Most Common Venue  
0           Shopping Mall  
1    Fast Food Restaurant  
2             Fish Market  
3  Thrift / Vintage Store  
4    Fast Food Restaurant

In [161]:
all_merged.shape

(347, 14)

Finally, let's visualize the resulting clusters

In [162]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(all_merged['Latitude'], all_merged['Longitude'], all_merged['Area'], all_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [163]:
for i in range(kclusters):
    print('The number of points in Cluster:', i, 'is', len(all_merged.loc[all_merged['Cluster Labels'] == i, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]))

The number of points in Cluster: 0 is 26
The number of points in Cluster: 1 is 22
The number of points in Cluster: 2 is 28
The number of points in Cluster: 3 is 1
The number of points in Cluster: 4 is 3
The number of points in Cluster: 5 is 1
The number of points in Cluster: 6 is 3
The number of points in Cluster: 7 is 29
The number of points in Cluster: 8 is 2
The number of points in Cluster: 9 is 1
The number of points in Cluster: 10 is 1
The number of points in Cluster: 11 is 1
The number of points in Cluster: 12 is 3
The number of points in Cluster: 13 is 1
The number of points in Cluster: 14 is 3
The number of points in Cluster: 15 is 6
The number of points in Cluster: 16 is 2
The number of points in Cluster: 17 is 2
The number of points in Cluster: 18 is 2
The number of points in Cluster: 19 is 1
The number of points in Cluster: 20 is 4
The number of points in Cluster: 21 is 2
The number of points in Cluster: 22 is 52
The number of points in Cluster: 23 is 1
The number of points 

In [164]:
cluster = int(all_merged.loc[all_merged['Area'] == original_loc['Area']]['Cluster Labels'])

In [165]:
ourpreferredcluster = all_merged.loc[all_merged['Cluster Labels'] == cluster].copy()
ourpreferredcluster

Area Latitude Longitude  Cluster Labels  \
32     Beaumaris South -37.9865   145.034               7   
63          Camberwell  -37.835   145.071               7   
71       Carlton South -37.8001   144.967               7   
73      Carnegie South  -37.835    144.96               7   
89    Cheltenham North -37.9593   145.067               7   
92   Clifton Hill East  -37.789   144.999               7   
100     Collins Street -37.8183   144.957               7   
102             Cotham -37.8086   145.046               7   
108            Darling -37.8385   144.992               7   
110           Deepdene -37.8131   145.068               7   
111    Degraves Street -37.8173   144.966               7   
114        Domain Road -37.8341   144.983               7   
116       Draytonville -37.8136   144.963               7   
173     Hawthorn North -37.8136   144.963               7   
189      Ivanhoe North -37.7703   145.046               7   
191         Kensington  -37.791   144.931               7   
195          Kew North -37.8053   145.036               7   
197         Kingsville  -37.809   144.878               7   
198   Kingsville South -37.8301    144.87               7   
204          Maidstone  -37.783   144.878               7   
251     North Brighton -37.9036   145.005               7   
272     Port Melbourne -37.8239   144.911               7   
274            Prahran  -37.852   144.998               7   
282        Regent West  28.0717  -80.6534               7   
307           St Kilda  -37.864   144.982               7   
308  St Kilda Junction -37.8552   144.983               7   
317        Stocksville -37.8676   145.105               7   
334        Toorak Road -37.8443   145.035               7   
346           Rosedale  43.6796  -79.3775               7   

    1st Most Common Venue  2nd Most Common Venue  3rd Most Common Venue  \
32                   Café          Grocery Store     Chinese Restaurant   
63          Train Station                   Park                   Café   
71     Italian Restaurant                   Café            Coffee Shop   
73                   Café                    Pub            Coffee Shop   
89                   Café             Playground     Athletics & Sports   
92                   Café   Gym / Fitness Center            Gas Station   
100                  Café            Coffee Shop    Japanese Restaurant   
102    Light Rail Station            Zoo Exhibit                Exhibit   
108                  Café     Italian Restaurant                  Hotel   
110                  Café                    Gym            Zoo Exhibit   
111                   Bar                   Café            Coffee Shop   
114    Light Rail Station      French Restaurant  Australian Restaurant   
116                  Café                    Bar            Coffee Shop   
173                  Café                    Bar            Coffee Shop   
189   Japanese Restaurant                   Café         Sandwich Place   
191                  Café                    Pub            Pizza Place   
195                  Café     Italian Restaurant   Fast Food Restaurant   
197                  Café     Italian Restaurant      Fish & Chips Shop   
198           Pizza Place      Indian Restaurant                 Bakery   
204                   Gym            Sports Club            Zoo Exhibit   
251           Coffee Shop                   Café          Movie Theater   
272              Bus Stop  Australian Restaurant            IT Services   
274                  Café                    Bar           Burger Joint   
282    Athletics & Sports            Zoo Exhibit                Exhibit   
307                  Café    Japanese Restaurant        Thai Restaurant   
308                  Café                  Hotel     Light Rail Station   
317                  Park            Pizza Place     Athletics & Sports   
334           Yoga Studio           Hockey Field                Dog Run   
346         

In [167]:
ourpreferredcluster.shape

(29, 14)

In [168]:
ourpreferredcluster_locations=ourpreferredcluster[['Area','Latitude',"Longitude"]]
ourpreferredcluster_locations.reset_index()

index               Area Latitude Longitude
0      32    Beaumaris South -37.9865   145.034
1      63         Camberwell  -37.835   145.071
2      71      Carlton South -37.8001   144.967
3      73     Carnegie South  -37.835    144.96
4      89   Cheltenham North -37.9593   145.067
5      92  Clifton Hill East  -37.789   144.999
6     100     Collins Street -37.8183   144.957
7     102             Cotham -37.8086   145.046
8     108            Darling -37.8385   144.992
9     110           Deepdene -37.8131   145.068
10    111    Degraves Street -37.8173   144.966
11    114        Domain Road -37.8341   144.983
12    116       Draytonville -37.8136   144.963
13    173     Hawthorn North -37.8136   144.963
14    189      Ivanhoe North -37.7703   145.046
15    191         Kensington  -37.791   144.931
16    195          Kew North -37.8053   145.036
17    197         Kingsville  -37.809   144.878
18    198   Kingsville South -37.8301    144.87
19    204          Maidstone  -37.783   144.878
20    251     North Brighton -37.9036   145.005
21    272     Port Melbourne -37.8239   144.911
22    274            Prahran  -37.852   144.998
23    282        Regent West  28.0717  -80.6534
24    307           St Kilda  -37.864   144.982
25    308  St Kilda Junction -37.8552   144.983
26    317        Stocksville -37.8676   145.105
27    334        Toorak Road -37.8443   145.035
28    346           Rosedale  43.6796  -79.3775

**Next we find the names of 5 hotels from our preferred cluster using Foursquare search query, which can be recommended on the basis that their neighbourhood is similar with Rosedale**

In [214]:

for row in range(0,26):
     
        LIMIT = 5
        radius = 500
        search_query = 'Hotel'  

        latitude=ourpreferredcluster['Latitude'].values[row]
        longitude=ourpreferredcluster['Longitude'].values[row]
 
        url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID,
                                                                                                                                                  CLIENT_SECRET,
                                                                                                                                                  latitude,
                                                                                                                                                  longitude,
                                                                                                                                                  VERSION,
                                                                                                                                                  search_query,
                                                                                                                                                  radius,
                                                                                                                                                  LIMIT)

        results = requests.get(url).json()
        selected_hotel = results['response']['venues']
        selected_hotel

In [218]:
df = pd.DataFrame(selected_hotel)
df
finaldf=df[["name", "location"]]
finaldf

name  \
0             Adina Apartment Hotel   
1               Quest Windsor Hotel   
2                  Park Regis Hotel   
3              Windsor Castle Hotel   
4  The Elephant & Wheelbarrow Hotel   

                                            location  
0  {'address': '157 Fitzroy St', 'crossStreet': '...  
1  {'address': '111 Punt Rd', 'lat': -37.85107890...  
2  {'address': '604 St. Kilda Rd.', 'lat': -37.85...  
3  {'address': '89 Albert St.', 'crossStreet': 'a...  
4  {'address': '169 Fitzroy St', 'crossStreet': '...